# Карта ОКН Великого Новгорода


**Дата**: 03.05.2023

**Авторы**: Деева Арина, Попова Ольга, Березанский Антон, Демиденко Арина

## 1. Импорт библиотек

In [107]:
!pip install pandas
!pip install folium
!pip install geopandas

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [108]:
import pandas as pd
import geopandas as gpd
import folium
from shapely import geometry
from folium.plugins import MarkerCluster

## 2. Загружаем данные

In [109]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [110]:
boundary = gpd.read_file('/content/drive/MyDrive/veln/boundary.geojson')
districts = gpd.read_file('/content/drive/MyDrive/veln/districts.geojson')
ancamble = gpd.read_file('/content/drive/MyDrive/veln/ancamble_ply.geojson')
points_okn = gpd.read_file('/content/drive/MyDrive/veln/okn_points.geojson')
houses_okn = gpd.read_file('/content/drive/MyDrive/veln/data_poly.geojson')

In [111]:
houses_okn.rename(columns = {'name':'Часть ансамбля'}, inplace = True )

In [112]:
ancamble.rename(columns = {'name':'Название ансамбля'}, inplace = True )
ancamble = ancamble[ancamble['official']!='no']

## 3. Визуализируем данные

In [113]:
#задаем стартовое окно отображения данных
points_okn = points_okn.to_crs('EPSG:4326')
m = folium.Map(location=[points_okn.centroid.y.mean(), points_okn.centroid.x.mean()], zoom_start=12,  tiles="cartodb positron", control_scale=True)

<ipython-input-113-9cced4f1f17c>:3: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  m = folium.Map(location=[points_okn.centroid.y.mean(), points_okn.centroid.x.mean()], zoom_start=12,  tiles="cartodb positron", control_scale=True)
<ipython-input-113-9cced4f1f17c>:3: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  m = folium.Map(location=[points_okn.centroid.y.mean(), points_okn.centroid.x.mean()], zoom_start=12,  tiles="cartodb positron", control_scale=True)


In [114]:
#добавляем полигон-границу городского округа
boundary_map = folium.GeoJson(
    boundary,
    name = "Velikiy Novgorod boundaries",
    style_function=lambda x:{
        "fillColor":"blue",
        "color": "blue",
        "weight": 0.8,
        "fillOpacity": 0,
    },
    highlight_function=lambda x: {"fillOpacity": 0},
    zoom_on_click=True,
    show=False,
).add_to(m)

In [115]:
m

In [116]:
! pip install jenkspy

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [117]:
import jenkspy

In [118]:
#добавляем условные районы
districts_map = folium.Choropleth(
    geo_data=districts,
    data = districts,
    columns = ['fid','ОКН_на_кв_км'],
    key_on = 'feature.properties.fid',
    fill_color = 'PuBu',
    legend_name = 'Amount of heritage sites per square kilometer',
    use_jenks=True,
    fill_opacity=0.3,
    line_weight=0.5,
    name="Districts"
).add_to(m)

districts_map.color_scale.width = 400

In [119]:
#добавляем ансамбли
ansamble_map = folium.GeoJson(
    ancamble,
    name = "Ansambles",
    style_function=lambda x:{
        "fillColor":"blue",
        "color": "blue",
        "weight": 0,
        "fillOpacity": 0.1,
    },
    highlight_function=lambda x: {"fillOpacity": 0.15},
    zoom_on_click=True,
    show=True,
    tooltip=folium.GeoJsonTooltip(fields=["Название ансамбля"]),
    popup=folium.GeoJsonPopup(fields=["Название ансамбля", "идентификатор ансамбля"]),
).add_to(m)

In [120]:
m

In [121]:
#добавляем полигоны зданий-ОКН
houses_okn_map = folium.GeoJson(
    houses_okn,
    name="Heritage buildings",
    tooltip=folium.GeoJsonTooltip(fields=["Объект"]),
    popup=folium.GeoJsonPopup(fields=["Объект", "Полный адрес", "дата создания", "Категория историко-культурного значения", "Часть ансамбля"]),
    style_function=lambda x: {
        "fillColor": 'blue',
        "color": "blue",
        "weight": 0.7,
        "fillOpacity": 0.4,
    },
    highlight_function=lambda x: {"fillOpacity": 0.8},
    zoom_on_click=True,
    show=False,
).add_to(m)

In [122]:
m

In [123]:
#добавляем кластеры точек
marker_cluster = MarkerCluster(name='Heritage Sites')
mc1= folium.plugins.FeatureGroupSubGroup(marker_cluster, 'Heritage Sites')
m.add_child(marker_cluster)
m.add_child(mc1)
mc1.add_child(folium.GeoJson(points_okn.to_json(), embed=False, show=False))

In [124]:
m

In [125]:
from folium.plugins import MousePosition
from folium.plugins import Fullscreen
from folium.plugins import MiniMap
from folium.plugins import Search
from folium.plugins import Geocoder

In [126]:
folium.LayerControl().add_to(m)

In [127]:
MousePosition().add_to(m)
Fullscreen(
    position="bottomright",
    title="Expand me",
    title_cancel="Exit me",
    force_separate_button=True,
).add_to(m)

In [128]:
minimap = MiniMap()
m.add_child(minimap)

In [129]:
folium.plugins.Geocoder(placeholder="Search for anything from OSM").add_to(m)

In [130]:
folium.plugins.Search(layer = houses_okn_map, geom_type="Polygon", placeholder="Search for OKN  House", search_label="Объект", collapsed=False, weight=3).add_to(m)

In [131]:
m

## 4. Сохраняем карту и готовим её к публикации

In [132]:
m.save("index.html")

In [133]:
from google.colab import files
files.download('index.html') 

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>